In [1]:
%pip install   \
    langchain \
    langchain-core\
    langchain-community \
    langchain-experimental \
    langchain-qdrant \
    qdrant-client \
    tiktoken \
    pymupdf 


Note: you may need to restart the kernel to use updated packages.


In [2]:
import os
import getpass

os.environ["OPENAI_API_KEY"] = getpass.getpass("OpenAI API Key:")

In [ ]:
from uuid import uuid4

os.environ["LANGCHAIN_TRACING_V2"] = "true"
os.environ["LANGCHAIN_PROJECT"] = f"AIE4 - LangGraph - {uuid4().hex[0:8]}"
os.environ["LANGCHAIN_API_KEY"] = getpass.getpass("LangSmith API Key: ")

In [57]:
from langchain_community.document_loaders import PyMuPDFLoader
from langchain.document_loaders import PyPDFium2Loader
# Additional content 
# https://arxiv.org/pdf/2306.12001
BOR_FILE_PATH = "https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf"
bor_documents = PyMuPDFLoader(file_path=BOR_FILE_PATH).load()

NIST_FILE_PATH = "https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf"
nist_documents = PyMuPDFLoader(file_path=NIST_FILE_PATH).load()

# PyPDFium2Loader_bor_documents = PyPDFium2Loader(file_path=BOR_FILE_PATH).load()
# PyPDFium2Loader_nist_documents = PyPDFium2Loader(file_path=NIST_FILE_PATH).load()

/opt/miniconda3/envs/llmops-course/lib/python3.11/site-packages/pypdfium2/_helpers/textpage.py:80: UserWarning: get_text_range() call with default params will be implicitly redirected to get_text_bounded()
  warnings.warn("get_text_range() call with default params will be implicitly redirected to get_text_bounded()")


In [4]:
bor_title = str(bor_documents[0].metadata.get("title"))
bor_title

'Blueprint for an AI Bill of Rights'

In [5]:
nist_title = str(nist_documents[0].metadata.get("title"))
nist_title

'Artificial Intelligence Risk Management Framework: Generative Artificial Intelligence Profile'

In [61]:
bor_documents[1]

Document(metadata={'source': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'file_path': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'page': 1, 'total_pages': 73, 'format': 'PDF 1.6', 'title': 'Blueprint for an AI Bill of Rights', 'author': '', 'subject': '', 'keywords': '', 'creator': 'Adobe Illustrator 26.3 (Macintosh)', 'producer': 'iLovePDF', 'creationDate': "D:20220920133035-04'00'", 'modDate': "D:20221003104118-04'00'", 'trapped': ''}, page_content=' \n \n \n \n \n \n \n \n \n \n \n \n \n \nAbout this Document \nThe Blueprint for an AI Bill of Rights: Making Automated Systems Work for the American People was \npublished by the White House Office of Science and Technology Policy in October 2022. This framework was \nreleased one year after OSTP announced the launch of a process to develop “a bill of rights for an AI-powered \nworld.” Its release follows a year of public engagement 

In [60]:
PyPDFium2Loader_bor_documents[1]

Document(metadata={'source': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'page': 1}, page_content='About this Document\r\nThe Blueprint for an AI Bill of Rights: Making Automated Systems Work for the American People was \r\npublished by the White House Office of Science and Technology Policy in October 2022. This framework was \r\nreleased one year after OSTP announced the launch of a process to develop “a bill of rights for an AI-powered \r\nworld.” Its release follows a year of public engagement to inform this initiative. The framework is available \r\nonline at: https://www.whitehouse.gov/ostp/ai-bill-of-rights\r\nAbout the Office of Science and Technology Policy\r\nThe Office of Science and Technology Policy (OSTP) was established by the National Science and Technology\r\nPolicy, Organization, and Priorities Act of 1976 to provide the President and others within the Executive Office \r\nof the President with advice on the scientif

In [123]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_experimental.text_splitter import SemanticChunker
from langchain.embeddings import HuggingFaceBgeEmbeddings
import tiktoken
from langchain_openai import OpenAIEmbeddings

# embedding_model = OpenAIEmbeddings(model="text-embedding-3-large")

# model_name = "BAAI/bge-large-en"
model_name = "gte-large-en-v1.5"
model_kwargs = {'device': 'cpu'}
encode_kwargs = {'normalize_embeddings': False}
embedding_model = HuggingFaceBgeEmbeddings(
    model_name=model_name,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs
)

def tiktoken_len(text):
    tokens = tiktoken.encoding_for_model("gpt-4o").encode(
        text,
    )
    return len(tokens)

# text_splitter = RecursiveCharacterTextSplitter(
#     chunk_size = 700,
#     chunk_overlap = 50,
#     length_function = len,
# )

text_splitter = SemanticChunker(embedding_model, breakpoint_threshold_type='percentile', breakpoint_threshold_amount=90)

bor_split_chunks = text_splitter.split_documents(bor_documents)
nist_split_chunks = text_splitter.split_documents(nist_documents)

# PDFium_bor_split_chunks = text_splitter.split_documents(PyPDFium2Loader_bor_documents)
# PDFium_nist_split_chunks = text_splitter.split_documents(PyPDFium2Loader_nist_documents)

/opt/miniconda3/envs/llmops-course/lib/python3.11/site-packages/pydantic/_internal/_fields.py:161: UserWarning: Field "model_name" has conflict with protected namespace "model_".

You may be able to resolve this warning by setting `model_config['protected_namespaces'] = ()`.
  warnings.warn(
/opt/miniconda3/envs/llmops-course/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/90.3k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/52.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/366 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/191 [00:00<?, ?B/s]

In [125]:
from langchain_qdrant import QdrantVectorStore
from qdrant_client import QdrantClient
from qdrant_client.http.models import Distance, VectorParams


client = QdrantClient(":memory:")
collection_name="ai-safety"
client.create_collection(
    collection_name=collection_name,
    vectors_config=VectorParams(size=1024, distance=Distance.COSINE),
)

vector_store = QdrantVectorStore(
    client=client,
    collection_name=collection_name,
    embedding=embedding_model,
)
vector_store.add_documents(bor_split_chunks+nist_split_chunks)

['9b10a85501bc48f18281e073417955fe',
 '9fc3056f3e72461399b0975a7d245af7',
 '907810cdcea641c491d6d9136e149603',
 'c4e2e16f06f34c78be93c427249618a4',
 '1a8886d120f74bfbbf8e314ad91195d7',
 '6c09482ef72b45d8882b9f8e53e8a0c6',
 '11bef1018ab943eca4239632a7f5cfb4',
 '17043a67b03b4cd6b53846c54f5da358',
 '209b3d4e2bf04a588da984cfa41d455d',
 'c9a7bdcbc1c84fc596f9c984334622dd',
 '628824299e584081aba7c5f7dce6f515',
 '2cbff63487124a65bd9605fc886ecb38',
 '8994b6fec3da447faf5267c1a4a6e98f',
 '498d23d9347f49ac9c61216ea042aefd',
 'e3071c284ffc40bf89bceb2063ee7b1d',
 '721a999c51074f3c90e767e6c5e08819',
 '9283571427654f7f99db9240403cfda2',
 'ab23c9db24494fb0839b8c0ea8a5e8cb',
 '2a62d4e74eff4ee9922aa5ffd4a2af82',
 '9c60b1358cea4047bf5ed5a4faacdbc0',
 '19de85ab2d24468590a1d0d5717581e2',
 '0dc02ab832194630abe6bc5581426b92',
 '8ae335a5f5734cc1aefa0e5ea38f253d',
 'edd41688cca64b34a694c1d027df45a6',
 '7004b933844b42ca8f6ab25ec87a95ef',
 '58890be93b5344e7beafb17d1a8c15d0',
 '9631f98644694f9789dfedd41fa1f5a9',
 

In [126]:
retriver = vector_store.as_retriever(
    search_type="similarity_score_threshold",
    search_kwargs={'k': 10,'score_threshold': 0.5}
    #  search_type="mmr",
    #             search_kwargs={'k': 8, 'fetch_k': 50}
)


In [127]:
from langchain.schema import BaseRetriever, Document
from pydantic import Field
from typing import List

class ContextEnrichedRetriever(BaseRetriever):
    # Declare fields using Pydantic's Field
    retriever: BaseRetriever = Field(...)
    window_size: int = Field(default=2)

    def __init__(self, retriever: BaseRetriever, window_size: int = 2):
        """
        A custom retriever that adds a context enrichment window to retrieved documents.
        Args:
        - retriever: The underlying retriever (e.g., Qdrant retriever).
        - window_size: Number of adjacent passages to include as context (before and after).
        """
        super().__init__(retriever=retriever, window_size=window_size)

    def enrich_context(self, document: Document, window_size: int) -> str:
        """
        Enrich the document context by adding the surrounding text (context window).
        Args:
        - document: The retrieved document.
        - window_size: Number of adjacent passages to include as context (before and after).
        """
        doc_text = document.page_content.split("\n")
        enriched_text = []
        for i, passage in enumerate(doc_text):
            context = doc_text[max(0, i - window_size):min(len(doc_text), i + window_size + 1)]
            enriched_text.append("\n".join(context))
        return "\n".join(enriched_text)

    def _get_relevant_documents(self, query: str) -> List[Document]:
        """
        Retrieve documents and apply context enrichment.
        Args:
        - query: The query string.
        Returns:
        - List of enriched documents.
        """
        documents = self.retriever.get_relevant_documents(query)
        enriched_documents = []
        for doc in documents:
            enriched_content = self.enrich_context(doc, self.window_size)
            enriched_doc = Document(page_content=enriched_content, metadata=doc.metadata)
            enriched_documents.append(enriched_doc)
        return enriched_documents

    async def _aget_relevant_documents(self, query: str) -> List[Document]:
        """
        Async version of the document retrieval and enrichment.
        Args:
        - query: The query string.
        Returns:
        - List of enriched documents.
        """
        documents = await self.retriever.aget_relevant_documents(query)
        enriched_documents = []
        for doc in documents:
            enriched_content = self.enrich_context(doc, self.window_size)
            enriched_doc = Document(page_content=enriched_content, metadata=doc.metadata)
            enriched_documents.append(enriched_doc)
        return enriched_documents


In [111]:
# todo: For some reason this creates duplicate need to debug this later.
context_enriched_retriever = ContextEnrichedRetriever(retriever=retriver, window_size=2)

In [128]:
docs = retriver.invoke("How can companies ensure AI does not violate data privacy laws?")
for i, doc in enumerate(docs):
    print(f"{i}: {doc.metadata.get('title')}")
    print(doc.page_content)

0: Blueprint for an AI Bill of Rights
In some cases, exceptions to 
the principles described in the Blueprint for an AI Bill of Rights may be necessary to comply with existing law, 
conform to the practicalities of a specific use case, or balance competing public interests. In particular, law 
enforcement, and other regulatory contexts may require government actors to protect civil rights, civil liberties, 
and privacy in a manner consistent with, but using alternate mechanisms to, the specific principles discussed in 
this framework. The Blueprint for an AI Bill of Rights is meant to assist governments and the private sector in 
moving principles into practice. The expectations given in the Technical Companion are meant to serve as a blueprint for the development of 
additional technical standards and practices that should be tailored for particular sectors and contexts. While 
existing laws informed the development of the Blueprint for an AI Bill of Rights, this framework does not de

In [129]:
# Trying Compression retriver
from langchain.retrievers import ContextualCompressionRetriever
from langchain.retrievers.document_compressors import LLMChainExtractor
from langchain_openai import ChatOpenAI

base_retriever = retriver

#Create a contextual compressor
compressor_llm = ChatOpenAI(temperature=0, model_name="gpt-4o", max_tokens=4000)
compressor = LLMChainExtractor.from_llm(compressor_llm)

#Combine the retriever with the compressor
compression_retriever = ContextualCompressionRetriever(
    base_compressor=compressor,
    base_retriever=base_retriever
)



In [130]:
compression_retriever.invoke("How can companies ensure AI does not violate data privacy laws?")

[Document(metadata={'source': 'https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf', 'file_path': 'https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf', 'page': 29, 'total_pages': 64, 'format': 'PDF 1.6', 'title': 'Artificial Intelligence Risk Management Framework: Generative Artificial Intelligence Profile', 'author': 'National Institute of Standards and Technology', 'subject': '', 'keywords': '', 'creator': 'Acrobat PDFMaker 24 for Word', 'producer': 'Adobe PDF Library 24.2.159', 'creationDate': "D:20240805141702-04'00'", 'modDate': "D:20240805143048-04'00'", 'trapped': '', '_id': '1ba549ad3b9b488ab15014c90b909ad1', '_collection_name': 'ai-safety'}, page_content='Conduct periodic monitoring of AI-generated content for privacy risks; address any possible instances of PII or sensitive data exposure. \n\nConnect new GAI policies, procedures, and processes to existing model, data, software development, and IT governance and to legal, compliance, and risk management activities. \n\n

In [131]:
from langchain.prompts import ChatPromptTemplate

base_rag_prompt_template = """\
You are a helpful assistant that can answer questions related to the provided context. Repond I don't have that information if outside context.

Context:
{context}

Question:
{question}
"""

base_rag_prompt = ChatPromptTemplate.from_template(base_rag_prompt_template)

In [132]:
from langchain_openai.chat_models import ChatOpenAI

base_llm = ChatOpenAI(model="gpt-4o", tags=["base_llm"])

In [133]:
from operator import itemgetter
from langchain.schema.output_parser import StrOutputParser
from langchain.schema.runnable import RunnablePassthrough

retrieval_augmented_qa_chain = (
    {"context": itemgetter("question") | compression_retriever, "question": itemgetter("question")}
    | RunnablePassthrough.assign(context=itemgetter("context"))
    | {"response": base_rag_prompt | base_llm, "context": itemgetter("context")}
)

In [134]:
result = retrieval_augmented_qa_chain.invoke({"question" : "How can companies ensure AI does not violate data privacy laws?"})

In [135]:
result.get('response').content

'Companies can ensure that AI does not violate data privacy laws by implementing several strategies and practices as mentioned in the provided context:\n\n1. **Periodic Monitoring**: Conduct regular monitoring of AI-generated content to identify and address any potential instances of personally identifiable information (PII) or sensitive data exposure. \n\n2. **Integration with Existing Policies**: Connect new AI policies, procedures, and processes with existing model, data, software development, and IT governance, as well as legal, compliance, and risk management activities.\n\n3. **Training Data Curation Policies**: Document training data curation policies in accordance with applicable laws and policies. This includes policies for the collection, retention, and minimum quality of data to mitigate risks such as the disclosure of inappropriate information, use of illegal or dangerous content, offensive cyber capabilities, data imbalances leading to harmful biases, and leaks of PII.\n\n

In [136]:
result

{'response': AIMessage(content='Companies can ensure that AI does not violate data privacy laws by implementing several strategies and practices as mentioned in the provided context:\n\n1. **Periodic Monitoring**: Conduct regular monitoring of AI-generated content to identify and address any potential instances of personally identifiable information (PII) or sensitive data exposure. \n\n2. **Integration with Existing Policies**: Connect new AI policies, procedures, and processes with existing model, data, software development, and IT governance, as well as legal, compliance, and risk management activities.\n\n3. **Training Data Curation Policies**: Document training data curation policies in accordance with applicable laws and policies. This includes policies for the collection, retention, and minimum quality of data to mitigate risks such as the disclosure of inappropriate information, use of illegal or dangerous content, offensive cyber capabilities, data imbalances leading to harmfu